# various statistics that can be calculated from GTFS

start with the model. Run the next cell, and then scroll down for all the interesting cells

In [31]:
from sqlalchemy import create_engine, func
from sqlalchemy.orm import sessionmaker
from sqlalchemy.ext.declarative import declarative_base
from sqlalchemy import Column, Unicode, Float, Boolean, Integer
Base = declarative_base()


class Agency(Base):
    """  https://developers.google.com/transit/gtfs/reference/#agencytxt """
    __tablename__ = 'agency'

    agency_id = Column(Integer, primary_key=True)
    agency_name = Column(Unicode)        # Human readable
    agency_url = Column(Unicode)
    agency_timezone = Column(Unicode)    # Always Asia/Jerusalem
    agency_lang = Column(Unicode)        # Always "he", even though it's wrong

    agency_phone = Column(Unicode)       # Unused
    agency_fare_url = Column(Unicode)    # Unused

    def __repr__(self):
        return f'<Agency {self.agency_id}>'

class Stop(Base):
    """  https://developers.google.com/transit/gtfs/reference/#stopstxt """
    __tablename__ = 'stops'

    stop_id = Column(Integer, primary_key=True)  # internal ID
    stop_code = Column(Unicode, index=True)      # code on the stop sign
    stop_name = Column(Unicode)                  # human readable
    stop_desc = Column(Unicode)                  # address
    stop_lat = Column(Float)
    stop_lon = Column(Float)
    location_type = Column(Integer)              # 0 = stop, 1 = station, 2 = station enterance
    parent_station = Column(Integer)             # for stops inside central stations
    zone_id = Column(Unicode)

    def __repr__(self):
        return f'<Stop #{self.stop_code}>'

class Route(Base):
    """  https://developers.google.com/transit/gtfs/reference/#routestxt """
    __tablename__ = 'routes'

    route_id = Column(Integer, primary_key=True)
    agency_id = Column(Integer)                     # Operator
    route_short_name = Column(Unicode, index=True)  # Actual "line number"
    route_long_name = Column(Unicode)
    route_desc = Column(Unicode)                    # Unused
    route_type = Column(Integer)                    # Bus / rail / etc
    route_color = Column(Unicode)                   # Used wrongly

    def __repr__(self):
        return f'<Route {self.route_id}>'

class Trip(Base):
    """  https://developers.google.com/transit/gtfs/reference/#tripsstxt """
    __tablename__ = 'trips'

    route_id = Column(Integer, index=True)
    service_id = Column(Integer)                   # Key for the Calendar table
    trip_id = Column(Unicode, primary_key=True)
    trip_headsign = Column(Unicode)                # "headsign" = on the front of the bus
    direction_id = Column(Integer)
    shape_id = Column(Integer)                     # Key for the shapes table

    def __repr__(self):
        return f'<Trip {self.trip_id}>'

class StopTime(Base):
    """  https://developers.google.com/transit/gtfs/reference/#stop_timestxt """
    __tablename__ = 'stoptimes'

    trip_id = Column(Unicode, primary_key=True, index=True)
    arrival_time = Column(Unicode, primary_key=True)
    departure_time = Column(Unicode)
    stop_id = Column(Integer, primary_key=True, index=True)
    stop_sequence = Column(Integer, primary_key=True)
    pickup_type = Column(Boolean)
    drop_off_type = Column(Boolean)
    shape_dist_traveled = Column(Unicode)

    def __repr__(self):
        template = '<StopTime trip={0},time={1},stop_id={2},sequence={3}>'
        return template.format(self.trip_id,
                               self.arrival_time,
                               self.stop_id,
                               self.stop_sequence)

class Shape(Base):
    """ https://developers.google.com/transit/gtfs/reference/#shapestxt """
    __tablename__ = 'shapes'
    shape_id = Column(Integer, primary_key=True, index=True)
    shape_pt_lat = Column(Float)
    shape_pt_lon = Column(Float)
    shape_pt_sequence = Column(Integer, primary_key=True)

class Calendar(Base):
    """ https://developers.google.com/transit/gtfs/reference/#calendartxt """
    __tablename__ = 'calendar'
    service_id = Column(Integer, primary_key=True, index=True)
    sunday = Column(Boolean)
    monday = Column(Boolean)
    tuesday = Column(Boolean)
    wednesday = Column(Boolean)
    thursday = Column(Boolean)
    friday = Column(Boolean)
    saturday = Column(Boolean)
    start_date = Column(Integer)
    end_date = Column(Integer)

class Translation(Base):
    """ GTFS Translations - a Google extension to the GTFS spec

    https://developers.google.com/transit/gtfs/reference/gtfs-extensions#translations
    """
    __tablename__ = 'translations'

    trans_id = Column(Unicode, primary_key=True, index=True)
    """ Translation ID - the source string """
    lang = Column(Unicode, primary_key=True)
    """ Translation language code """
    translation = Column(Unicode)
    """ Translated string """

    def __str__(self):
        return self.translation

    def __repr__(self):
        return '<Translation of %s (to %s): %s>' % (self.trans_id, self.lang,
                                                    self.translation)

engine = create_engine("postgresql:///gtfs")
Base.metadata.create_all(engine)
session = sessionmaker(bind=engine)()


# A Sense of Scale
## How many lines, stops, operators

In [3]:
stops = session.query(Stop).count()
operators = session.query(Agency).count()

# Counting routes is a bit different. I don't want to count multiple directions / alternatives as extra lines
# so I'm using route_desc, which countains the route license number.
# A license number looks like this: 10014-3-פ
# The first part is the actual license nnumber, the second is the "direction code" and the third is "alternative code".
# see this for more info: http://israelbikebus.blogspot.com/2013/12/blog-post_31.html
routes = session.query(func.split_part(Route.route_desc, '-', 1)).distinct().count()

print(f"{operators} Operators")
print(f"{routes} Routes")
print(f"{stops} Stops")


26 Operators
2644 Routes
27530 Stops


## Trips per Day

In [4]:
from datetime import date
today = int(date.today().strftime("%Y%m%d"))
today_name = date.today().strftime("%A").lower()
trips = session.query(Trip, Calendar).join(Calendar, Trip.service_id == Calendar.service_id)\
                                     .filter(Calendar.start_date <= today, Calendar.end_date >= today)

# I'm sure there's a more efficient way to do this
total = 0
for trip,calendar in trips.all():
    if getattr(calendar, today_name): 
        total += 1

print(f"{total} Trips today")

88665 Trips today


## Total Length

In [32]:
# ALTER TABLE shapes ADD COLUMN geom geography(POINT,2039);
# UPDATE shapes SET geom = ST_MakePoint(shape_pt_lon,shape_pt_lat);




KeyboardInterrupt: 

# Lines With Most Stops

In [33]:
query = """SELECT DISTINCT max(stop_sequence) AS stops,routes.route_short_name,routes.route_long_name,agency_name
           FROM stoptimes as st
           JOIN trips ON trips.trip_id=st.trip_id
           JOIN routes ON trips.route_id=routes.route_id
           JOIN agency ON routes.agency_id=agency.agency_id
           GROUP BY routes.route_id,agency.agency_name
           ORDER BY stops DESC LIMIT 20;"""

print("stops, line, where, operator")
for item in session.execute(query):
    print(item)

stops, line, where, operator
(112, '373', 'ת. מרכזית רחובות/רציפים-רחובות<->הרצל/קיבוץ גלויות-אופקים-1#', 'מטרופולין')
(108, '200', 'חוף דדו-חיפה<->חלוצי התעשייה/הגומא-חיפה-1#', 'אגד')
(108, '200', 'חוף דדו-חיפה<->חלוצי התעשייה/הגומא-חיפה-1ב', 'אגד')
(108, '373', 'שד. הרצל/הנשיא-אופקים<->ת. מרכזית רחובות/הורדה-רחובות-2#', 'מטרופולין')
(106, '343', 'העיר העתיקה-עכו<->חניון נצרת עילית-נצרת עילית-2#', 'אגד')
(105, '211', 'הקישון / איילון-בית שמש<->מסוף רידינג-תל אביב יפו-10', 'סופרבוס')
(105, '211', 'ח.רידינג-תל אביב יפו<->שד.נחל הקישון/נחל שחם-בית שמש-20', 'סופרבוס')
(105, '343', 'וייצמן/יוסף טרומפלדור-עכו<->חניון נצרת עילית-נצרת עילית-2ש', 'אגד')
(105, '343', 'חניון אגד/העבודה-נצרת עילית<->העיר העתיקה-עכו-1#', 'אגד')
(104, '343', 'חניון אגד/העבודה-נצרת עילית<->וייצמן/מעלה החורשה-עכו-1ש', 'אגד')
(103, '840', "ת.מרכזית ת''א ק.7/רציפים-תל אביב יפו<->ת. מרכזית ק''ש/הורדה-קרית שמונה-1#", 'אגד')
(103, '966', 'שיאון/טיילת נווה-קצרין<->ת. מרכזית י-ם/הורדה-ירושלים-2#', 'אגד')
(102, '14', 'רכבל/ה

# Most Frequent Lines
according to how many trips per day

In [42]:
from datetime import date
today = int(date.today().strftime("%Y%m%d"))
today_name = date.today().strftime("%A").lower()
trips = session.query(Trip, Calendar, Route, Agency).join(Calendar, Trip.service_id == Calendar.service_id)\
                                                    .join(Route, Trip.route_id == Route.route_id)\
                                                    .join(Agency, Route.agency_id == Agency.agency_id)\
                                                    .filter(Calendar.start_date <= today, Calendar.end_date >= today)

# I'm sure there's a more efficient way to do this
lines = {}
for trip,calendar,route,agency in trips.all():
    if not getattr(calendar, today_name): 
        continue
    if route.route_id in lines:
        lines[route.route_id]['count'] += 1
    else:
        lines[route.route_id] = {'count': 1,
                                 'operator': agency.agency_name,
                                 'route_short_name': route.route_short_name,
                                 'route_log_name': route.route_long_name}

for route  in sorted(lines.values(), key=lambda r: r['count'], reverse=True):
    print(route)

{'count': 213, 'operator': 'דן צפון', 'route_short_name': '1', 'route_log_name': 'מרכזית הקריות-קרית מוצקין<->ת. מרכזית חוף הכרמל/הורדה מטרונית-חיפה-20'}
{'count': 213, 'operator': 'דן צפון', 'route_short_name': '1', 'route_log_name': 'ת. מרכזית חוף הכרמל/רציפים עירוני-חיפה<->מרכזית הקריות-קרית מוצקין-10'}
{'count': 164, 'operator': 'דן', 'route_short_name': '1', 'route_log_name': "ת. מרכזית פ''ת/רציפים עירוני-פתח תקווה<->מרכז הספורט-בת ים-10"}
{'count': 163, 'operator': 'דן', 'route_short_name': '1', 'route_log_name': "מרכז הספורט/דרך בגין-בת ים<->ת. מרכזית פ''ת/רציפים עירוני-פתח תקווה-20"}
{'count': 154, 'operator': 'דן', 'route_short_name': '5', 'route_log_name': "ת.מרכזית ת''א ק.4/רציפים-תל אביב יפו<->ת. רכבת ת''א מרכז/חנה וסע-תל אביב יפו-10"}
{'count': 153, 'operator': 'דן', 'route_short_name': '5', 'route_log_name': "ת. רכבת ת''א מרכז/על פרשת דרכים-תל אביב יפו<->ת. מרכזית ת''א ק. 4/הורדה-תל אביב יפו-20"}
{'count': 149, 'operator': 'דן', 'route_short_name': '204', 'route_log_name'

{'count': 5, 'operator': 'קווים', 'route_short_name': '70', 'route_log_name': 'ת. מרכזית חדרה/רציפים-חדרה<->הנדיב/המייסדים-זכרון יעקב-11'}
{'count': 5, 'operator': 'סופרבוס', 'route_short_name': '6', 'route_log_name': 'ת. מרכזית עפולה-עפולה<->בית עלמין עפולה-עפולה-10'}
{'count': 5, 'operator': 'סופרבוס', 'route_short_name': '6', 'route_log_name': 'בית עלמין עפולה-עפולה<->ת. מרכזית עפולה/הורדה-עפולה-20'}
{'count': 5, 'operator': 'אפיקים', 'route_short_name': '87', 'route_log_name': "ת. מרכזית פ''ת/רציפים אזורי-פתח תקווה<->שיב''א-רמת גן-11"}
{'count': 5, 'operator': 'אפיקים', 'route_short_name': '87', 'route_log_name': "שיב''א-רמת גן<->ת. מרכזית פ''ת/הורדה-פתח תקווה-21"}
{'count': 5, 'operator': 'ש.א.מ', 'route_short_name': '18', 'route_log_name': '10297-ריינה<->10297-ריינה-3ג'}
{'count': 5, 'operator': 'נסיעות ותיירות', 'route_short_name': '29', 'route_log_name': 'בסיס מחווה אלון-מרום הגליל<->תחנה מרכזית-נצרת-2#'}
{'count': 5, 'operator': 'נסיעות ותיירות', 'route_short_name': '30', 'rou

# Stops by Number of Lines

In [65]:
stops = []
for stop in session.query(Stop).all():
    routes_in_stop = session.query(Route).join(Trip, Trip.route_id == Route.route_id)\
                                         .join(StopTime, StopTime.trip_id == Trip.trip_id)\
                                         .filter(StopTime.stop_id == stop.stop_id)\
                                         .distinct().count()
    stops.append({"code": stop.stop_code, "name": stop.stop_name, "routes": routes_in_stop})

for stop in sorted(stops, key=lambda s: s['routes'], reverse=True):
    print(stop)

{'code': '17038', 'name': 'תל אביב מרכז', 'routes': 177}
{'code': '21472', 'name': 'קניון עזריאלי/דרך בגין', 'routes': 171}
{'code': '5059', 'name': 'ירמיהו/אלקנה', 'routes': 150}
{'code': '15657', 'name': "ת. מרכזית ב''ש", 'routes': 141}
{'code': '17036', 'name': 'תא אוניברסיטה', 'routes': 141}
{'code': '5058', 'name': 'ירמיהו/מנחת יצחק', 'routes': 139}
{'code': '17104', 'name': 'תל אביב ההגנה', 'routes': 138}
{'code': '4014', 'name': 'ירמיהו/מנחת יצחק', 'routes': 133}
{'code': '21675', 'name': 'גשר קלקא/דרך בגין', 'routes': 133}
{'code': '4013', 'name': 'ירמיהו/אלקנה', 'routes': 129}
{'code': '28627', 'name': "ת. מרכזית ת''א ק. 6/הורדה", 'routes': 129}
{'code': '5060', 'name': 'בר אילן/רבנו גרשום', 'routes': 126}
{'code': '17046', 'name': 'השלום', 'routes': 124}
{'code': '25071', 'name': 'סמינר הקיבוצים/דרך נמיר', 'routes': 120}
{'code': '17024', 'name': 'בנימינה', 'routes': 113}
{'code': '21188', 'name': 'דרך נמיר/יהודה המכבי', 'routes': 110}
{'code': '21221', 'name': 'גשר קלקא/דרך 

{'code': '31430', 'name': 'כביש 412/שדרות מנחם בגין', 'routes': 19}
{'code': '31441', 'name': 'לוי אשכול/חסידי אומות העולם', 'routes': 19}
{'code': '31571', 'name': 'כביש 461 / נווה מונוסון', 'routes': 19}
{'code': '31638', 'name': 'צומת יהוד מערב/כביש 461', 'routes': 19}
{'code': '32221', 'name': 'שד. הסנהדרין/שד. ירושלים', 'routes': 19}
{'code': '32245', 'name': "דוד וולפסון/רמב''ם", 'routes': 19}
{'code': '32652', 'name': 'יהודה הלוי/מלכי ישראל', 'routes': 19}
{'code': '32759', 'name': 'שד. עמק איילון - כיכר אנפה', 'routes': 19}
{'code': '32774', 'name': 'חברת חשמל/משה דיין', 'routes': 19}
{'code': '32909', 'name': "ז'בוטינסקי/א.צ גרינברג", 'routes': 19}
{'code': '46953', 'name': 'הרקפות/הכלניות', 'routes': 19}
{'code': '47274', 'name': "בי''ס מיתרים/שקדים", 'routes': 19}
{'code': '50537', 'name': 'צומת מעלות', 'routes': 19}
{'code': '50625', 'name': 'צומת תפן', 'routes': 19}
{'code': '50638', 'name': "שד. מ''ג המעפילים/כלנית", 'routes': 19}
{'code': '51277', 'name': 'המעוף/הר וגיא'

{'code': '33736', 'name': 'מחלף שפירים/כביש 412', 'routes': 11}
{'code': '33823', 'name': 'לוי אשכול/כיכר הלוחמים', 'routes': 11}
{'code': '33845', 'name': 'דרך רמתיים/משה שרת', 'routes': 11}
{'code': '33846', 'name': 'צומת נבלט', 'routes': 11}
{'code': '33870', 'name': 'צומת בית ברל', 'routes': 11}
{'code': '33871', 'name': 'אולם ספורט/בית ברל', 'routes': 11}
{'code': '34105', 'name': 'זכריה הנביא/עמק האלה', 'routes': 11}
{'code': '34154', 'name': 'עמק איילון/תלתן', 'routes': 11}
{'code': '34180', 'name': 'שדרות המכבים/דרך פלד', 'routes': 11}
{'code': '34257', 'name': 'צומת צופית', 'routes': 11}
{'code': '34285', 'name': 'דוד אלעזר/השיזף', 'routes': 11}
{'code': '34288', 'name': "ירושלים/לח''י", 'routes': 11}
{'code': '34289', 'name': 'ירושלים/זכריה מדאר', 'routes': 11}
{'code': '34290', 'name': 'מחנה נחל שורק', 'routes': 11}
{'code': '34541', 'name': 'צומת זמר', 'routes': 11}
{'code': '34842', 'name': 'התעשיה/הסדנא', 'routes': 11}
{'code': '35052', 'name': 'תלתן/קיפודן', 'routes': 11

{'code': '22925', 'name': 'מסוף רידינג', 'routes': 7}
{'code': '25205', 'name': "יפת/הבעש''ט", 'routes': 7}
{'code': '25224', 'name': 'יפת/מנדס פראנס', 'routes': 7}
{'code': '25252', 'name': 'גרינבוים/מאיר גרוסמן', 'routes': 7}
{'code': '25258', 'name': "ביה''ס ברנר/מאיר גרוסמן", 'routes': 7}
{'code': '25277', 'name': "שד' ישראל גורי/גיתית", 'routes': 7}
{'code': '25279', 'name': "שד' ישראל גורי/דיק", 'routes': 7}
{'code': '25281', 'name': "קופ''ח כללית/שד' ישראל גורי", 'routes': 7}
{'code': '25433', 'name': "שד' הר ציון/וולפסון", 'routes': 7}
{'code': '25476', 'name': 'לוינסקי/לבנדה', 'routes': 7}
{'code': '25532', 'name': 'אלנבי/הכובשים', 'routes': 7}
{'code': '25537', 'name': 'בן יהודה/טרומפלדור', 'routes': 7}
{'code': '25584', 'name': "שד' רוטשילד/בלפור", 'routes': 7}
{'code': '25682', 'name': "יגאל אלון/שד' החי''ל", 'routes': 7}
{'code': '25779', 'name': 'דיזנגוף/גורדון', 'routes': 7}
{'code': '25833', 'name': 'דיזנגוף/בזל', 'routes': 7}
{'code': '25899', 'name': 'ויצמן/פנקס', 'ro

{'code': '33942', 'name': 'יצחק שדה/מניה שוחט', 'routes': 5}
{'code': '33943', 'name': "יצחק שדה/ז'בוטינסקי", 'routes': 5}
{'code': '33959', 'name': 'העצמאות/סנהדרין', 'routes': 5}
{'code': '33996', 'name': 'גורודסקי/מרגולין', 'routes': 5}
{'code': '34042', 'name': "ד''ר מרדכי וחווה פרימן/החלוץ", 'routes': 5}
{'code': '34069', 'name': 'צומת בית נחמיה', 'routes': 5}
{'code': '34113', 'name': 'מרדכי (מוטה) גור/עמק בית שאן', 'routes': 5}
{'code': '34140', 'name': 'עמק דותן/לבונה', 'routes': 5}
{'code': '34147', 'name': 'שדרות ירושלים/פרופסור שור', 'routes': 5}
{'code': '34314', 'name': 'כצנלסון/קפלן אליעזר', 'routes': 5}
{'code': '34380', 'name': "מג''ב משמר אילון", 'routes': 5}
{'code': '34381', 'name': "מג''ב משמר אילון", 'routes': 5}
{'code': '34405', 'name': 'המרכבה/המלאכה', 'routes': 5}
{'code': '34443', 'name': 'קופת חולים/פינסקר', 'routes': 5}
{'code': '34518', 'name': 'המרכבה/הבנאי', 'routes': 5}
{'code': '34519', 'name': 'חצי חינם/המרכבה', 'routes': 5}
{'code': '34564', 'name': '

{'code': '59199', 'name': 'נחף מרכז', 'routes': 3}
{'code': '59200', 'name': 'נחף מסגד', 'routes': 3}
{'code': '59219', 'name': 'קופת חולים כללית', 'routes': 3}
{'code': '59220', 'name': 'מרפאה', 'routes': 3}
{'code': '59221', 'name': 'אבו סנאן 115/110', 'routes': 3}
{'code': '59246', 'name': 'מועצה מקומית', 'routes': 3}
{'code': '59247', 'name': 'נחף דואר', 'routes': 3}
{'code': '59248', 'name': 'קופת חולים כללית', 'routes': 3}
{'code': '59249', 'name': 'בית ספר א', 'routes': 3}
{'code': '59256', 'name': 'קופת חולים כללית', 'routes': 3}
{'code': '59257', 'name': 'מרפאה', 'routes': 3}
{'code': '59259', 'name': 'קופת חולים', 'routes': 3}
{'code': '59260', 'name': 'חומרי בנין', 'routes': 3}
{'code': '59261', 'name': 'צומת המעיין', 'routes': 3}
{'code': '59262', 'name': 'חומרי בנין', 'routes': 3}
{'code': '59263', 'name': "כיכר סאג'ור", 'routes': 3}
{'code': '59264', 'name': 'קופת חולים', 'routes': 3}
{'code': '59268', 'name': 'צומת בית עלמין', 'routes': 3}
{'code': '59269', 'name': 'צומת

{'code': '26235', 'name': "מולכו/שד' ירושלים", 'routes': 2}
{'code': '26269', 'name': "ביאליק/דרך ז'בוטינסקי", 'routes': 2}
{'code': '26298', 'name': 'קאנטרי דקל', 'routes': 2}
{'code': '26331', 'name': 'קריניצי/הרצל', 'routes': 2}
{'code': '26342', 'name': 'דרך בן גוריון/מגדים', 'routes': 2}
{'code': '26373', 'name': "הרא''ה/חיבת ציון", 'routes': 2}
{'code': '26375', 'name': "הרא''ה/שד' ירושלים", 'routes': 2}
{'code': '26381', 'name': 'עיריית בני ברק/ירושלים', 'routes': 2}
{'code': '26435', 'name': 'קהילת ורשה/שלום אש', 'routes': 2}
{'code': '26446', 'name': 'קהילת יאסי/פנחס רוזן', 'routes': 2}
{'code': '26457', 'name': 'משמר הירדן/הרוגי מלכות', 'routes': 2}
{'code': '26534', 'name': 'הרב בר אילן', 'routes': 2}
{'code': '26659', 'name': 'קריית חינוך', 'routes': 2}
{'code': '26662', 'name': 'סי אנד סאן/רוזנבלום', 'routes': 2}
{'code': '26732', 'name': "צה''ל/משה סנה", 'routes': 2}
{'code': '26734', 'name': "ביה''ס און/וייסבורג", 'routes': 2}
{'code': '26735', 'name': "ביה''ס און/וייסבו

{'code': '59082', 'name': 'הורד/יקינטון', 'routes': 1}
{'code': '59083', 'name': 'יקינטון/משעול הברוש', 'routes': 1}
{'code': '59090', 'name': 'עראמשה ה', 'routes': 1}
{'code': '59092', 'name': 'עראמשה ד', 'routes': 1}
{'code': '59093', 'name': 'עראמשה 3', 'routes': 1}
{'code': '59094', 'name': 'עראמשה ועד מקומי', 'routes': 1}
{'code': '59116', 'name': 'תשרי/חשון', 'routes': 1}
{'code': '59138', 'name': 'הגפן/התאנה', 'routes': 1}
{'code': '59149', 'name': 'תשרי/כסלו', 'routes': 1}
{'code': '59178', 'name': 'מרכז מסחרי/864', 'routes': 1}
{'code': '59213', 'name': 'נוף כנרת/נוף החולה', 'routes': 1}
{'code': '59222', 'name': 'אבו סנאן 101', 'routes': 1}
{'code': '59275', 'name': 'מסעף איילת השחר', 'routes': 1}
{'code': '59298', 'name': 'תצפית/864', 'routes': 1}
{'code': '59312', 'name': 'מעונה ז', 'routes': 1}
{'code': '59319', 'name': "הרצל/יאנוש קורצ'אק", 'routes': 1}
{'code': '59326', 'name': 'אודם/שד. הנשיא הרצוג', 'routes': 1}
{'code': '59332', 'name': 'עראמשה מרכז', 'routes': 1}
{'c

## Stops by Number of Lines in Tel Aviv

In [67]:
stops = []
for stop in session.query(Stop).filter(Stop.stop_desc.like('%עיר: תל אביב יפו%')).all():
    routes_in_stop = session.query(Route).join(Trip, Trip.route_id == Route.route_id)\
                                         .join(StopTime, StopTime.trip_id == Trip.trip_id)\
                                         .filter(StopTime.stop_id == stop.stop_id)\
                                         .distinct().count()
    stops.append({"code": stop.stop_code, "name": stop.stop_name, "routes": routes_in_stop})

for stop in sorted(stops, key=lambda s: s['routes'], reverse=True):
    print(stop)

{'code': '17038', 'name': 'תל אביב מרכז', 'routes': 177}
{'code': '21472', 'name': 'קניון עזריאלי/דרך בגין', 'routes': 171}
{'code': '17036', 'name': 'תא אוניברסיטה', 'routes': 141}
{'code': '17104', 'name': 'תל אביב ההגנה', 'routes': 138}
{'code': '21675', 'name': 'גשר קלקא/דרך בגין', 'routes': 133}
{'code': '28627', 'name': "ת. מרכזית ת''א ק. 6/הורדה", 'routes': 129}
{'code': '17046', 'name': 'השלום', 'routes': 124}
{'code': '25071', 'name': 'סמינר הקיבוצים/דרך נמיר', 'routes': 120}
{'code': '21188', 'name': 'דרך נמיר/יהודה המכבי', 'routes': 110}
{'code': '21221', 'name': 'גשר קלקא/דרך בגין', 'routes': 109}
{'code': '20349', 'name': 'דרך נמיר/ארלוזורוב', 'routes': 93}
{'code': '23014', 'name': 'קניון עזריאלי/דרך בגין', 'routes': 87}
{'code': '20047', 'name': 'דרך נמיר/אינשטיין', 'routes': 85}
{'code': '24068', 'name': "ת. רכבת ת''א מרכז/דרך נמיר", 'routes': 79}
{'code': '28660', 'name': "בי''ס שבח מופת/המסגר", 'routes': 76}
{'code': '20105', 'name': 'קרית חינוך/דרך נמיר', 'routes': 7

# Stops by Frequency

warning, this code is extremely inefficient and requires quite a lot of memory to complete

In [9]:
from datetime import date
today = int(date.today().strftime("%Y%m%d"))
today_name = date.today().strftime("%A").lower()
trips = session.query(Stop, Trip, Calendar).join(StopTime, Stop.stop_id  == StopTime.stop_id)\
                                           .join(Trip, Trip.trip_id == StopTime.trip_id)\
                                           .join(Calendar, Calendar.service_id == Trip.service_id)\
                                           .filter(Calendar.start_date <= today, Calendar.end_date >= today)

# I'm sure there's a more efficient way to do this
stops = {}
for stop,trip,calendar in trips.all():
    if not getattr(calendar, today_name): 
        continue
    if stop.stop_id in stops:
        stops[stop.stop_id]['count'] += 1
    else:
        stops[stop.stop_id] = {'count': 1,
                               'code': stop.stop_code,
                               'name': stop.stop_name,
                               'address': stop.stop_desc}

for stop  in sorted(stops.values(), key=lambda r: r['count'], reverse=True):
    print(stop)

{'count': 2553, 'code': '21472', 'name': 'קניון עזריאלי/דרך בגין', 'address': ' רחוב:דרך מנחם בגין  עיר: תל אביב יפו רציף:   קומה:  '}
{'count': 2335, 'code': '21675', 'name': 'גשר קלקא/דרך בגין', 'address': ' רחוב:מרדכי מקלף 5 עיר: תל אביב יפו רציף:   קומה:  '}
{'count': 2084, 'code': '21221', 'name': 'גשר קלקא/דרך בגין', 'address': ' רחוב:דרך מנחם בגין 122 עיר: תל אביב יפו רציף:   קומה:  '}
{'count': 1812, 'code': '4014', 'name': 'ירמיהו/מנחת יצחק', 'address': ' רחוב:ירמיהו 24 עיר: ירושלים רציף:   קומה:  '}
{'count': 1806, 'code': '5059', 'name': 'ירמיהו/אלקנה', 'address': ' רחוב:ירמיהו 3 עיר: ירושלים רציף:   קומה:  '}
{'count': 1684, 'code': '21188', 'name': 'דרך נמיר/יהודה המכבי', 'address': ' רחוב:דרך נמיר 127 עיר: תל אביב יפו רציף:   קומה:  '}
{'count': 1680, 'code': '25071', 'name': 'סמינר הקיבוצים/דרך נמיר', 'address': ' רחוב:דרך נמיר  עיר: תל אביב יפו רציף:   קומה:  '}
{'count': 1628, 'code': '5200', 'name': 'בנייני האומה', 'address': " רחוב:שדרות שז''ר  עיר: ירושלים רציף:   ק

{'count': 274, 'code': '52047', 'name': 'מגן דוד אדום/מעלה יצחק', 'address': ' רחוב:שדרות מעלה יצחק  עיר: נצרת עילית רציף:   קומה:  '}
{'count': 274, 'code': '42661', 'name': 'וינשל/ולנברג', 'address': ' רחוב:דרך ויינשל  עיר: חיפה רציף:   קומה:  '}
{'count': 274, 'code': '33897', 'name': 'שדרות ירושלים/סוקולוב', 'address': ' רחוב:שדרות ירושלים 16 עיר: חולון רציף:   קומה:  '}
{'count': 274, 'code': '916', 'name': 'קוסטריקה א', 'address': ' רחוב:קוסטה ריקה 58 עיר: ירושלים רציף:   קומה:  '}
{'count': 274, 'code': '909', 'name': "'קוסטה ריקה ב", 'address': ' רחוב:קוסטה ריקה 63 עיר: ירושלים רציף:   קומה:  '}
{'count': 274, 'code': '1210', 'name': 'קוסטה ריקה ה', 'address': ' רחוב:קוסטה ריקה 17 עיר: ירושלים רציף:   קומה:  '}
{'count': 274, 'code': '5870', 'name': "'קוסטה ריקה ב", 'address': ' רחוב:קוסטה ריקה 44 עיר: ירושלים רציף:   קומה:  '}
{'count': 274, 'code': '1529', 'name': "'קוסטה ריקה א", 'address': ' רחוב:קוסטה ריקה 54 עיר: ירושלים רציף:   קומה:  '}
{'count': 274, 'code': '3336', 'n

{'count': 170, 'code': '13526', 'name': "בית נועם/שדרות שז''ר", 'address': " רחוב:שדרות שז''ר 18 עיר: באר שבע רציף:   קומה:  "}
{'count': 169, 'code': '33702', 'name': 'מחלף גדרה', 'address': ' רחוב:  עיר: גדרה רציף:   קומה:  '}
{'count': 169, 'code': '51445', 'name': 'תל-חי/הנרייטה סאלד', 'address': ' רחוב:תל חי  עיר: קרית שמונה רציף:   קומה:  '}
{'count': 169, 'code': '41873', 'name': 'שדרות חן/הנס מולר', 'address': " רחוב:שדרות ח''ן  עיר: קרית ביאליק רציף:   קומה:  "}
{'count': 169, 'code': '41432', 'name': 'שדרות חן/יוסף לוי', 'address': " רחוב:שדרות ח''ן 7 עיר: קרית ביאליק רציף:   קומה:  "}
{'count': 169, 'code': '41024', 'name': 'המלך דוד/אצל', 'address': ' רחוב:המלך דוד 33 עיר: חיפה רציף:   קומה:  '}
{'count': 169, 'code': '32250', 'name': 'ת. רכבת ראשונים', 'address': ' רחוב:הרצל  עיר: ראשון לציון רציף:   קומה:  '}
{'count': 169, 'code': '33561', 'name': 'דרך מנחם בגין/כורש', 'address': ' רחוב:דרך מנחם בגין  עיר: בת ים רציף:   קומה:  '}
{'count': 169, 'code': '36093', 'name': '

{'count': 106, 'code': '5735', 'name': 'בית חולים מקאסד כניסה ראשית/ראבעה אל עדוויה', 'address': ' רחוב:רבעה אל עדוויה  עיר: ירושלים רציף:   קומה:  '}
{'count': 106, 'code': '35290', 'name': 'צומת יד בנימין', 'address': ' רחוב:3  עיר: מטה יהודה רציף:   קומה:  '}
{'count': 106, 'code': '53408', 'name': 'מסוף חצור הגלילית/רציפים', 'address': ' רחוב:  עיר: חצור הגלילית רציף: 3   קומה:  '}
{'count': 106, 'code': '46216', 'name': 'ת. רכבת חוף הכרמל', 'address': ' רחוב:אנדרי סחרוב  עיר: חיפה רציף:   קומה:  '}
{'count': 106, 'code': '3281', 'name': 'משה קול/מרה', 'address': ' רחוב:משה קול 51 עיר: ירושלים רציף:   קומה:  '}
{'count': 106, 'code': '3282', 'name': 'משה קול/דינור', 'address': ' רחוב:משה קול 37 עיר: ירושלים רציף:   קומה:  '}
{'count': 106, 'code': '60857', 'name': 'נופי הסלע/החלמיש', 'address': ' רחוב:נופי הסלע 82 עיר: מעלה אדומים רציף:   קומה:  '}
{'count': 106, 'code': '60942', 'name': 'החלמיש/הרכס', 'address': ' רחוב:החלמיש 2 עיר: מעלה אדומים רציף:   קומה:  '}
{'count': 106, 'co

{'count': 68, 'code': '21500', 'name': "דרך זאב ז'בוטינסקי/מכון מור", 'address': " רחוב:דרך זאב ז'בוטינסקי  עיר: בני ברק רציף:   קומה:  "}
{'count': 68, 'code': '57310', 'name': 'חרצית/חלמונית', 'address': ' רחוב:חרצית  עיר: טבריה רציף:   קומה:  '}
{'count': 68, 'code': '47017', 'name': 'שכונה מערבית', 'address': ' רחוב:  עיר: עספיא רציף:   קומה:  '}
{'count': 68, 'code': '57907', 'name': 'עמק השלום/הגלעד', 'address': ' רחוב:עמק השלום 48 עיר: יקנעם עילית רציף:   קומה:  '}
{'count': 68, 'code': '54848', 'name': 'עיריית בית שאן', 'address': ' רחוב:  עיר: בית שאן רציף:   קומה:  '}
{'count': 68, 'code': '39403', 'name': 'הארז/השלדג', 'address': ' רחוב:הארז 20 עיר: קדימה צורן רציף:   קומה:  '}
{'count': 68, 'code': '40482', 'name': 'גפן/תמר', 'address': ' רחוב:גפן 37 עיר: חריש רציף:   קומה:  '}
{'count': 68, 'code': '40473', 'name': 'גפן/תאנה', 'address': ' רחוב:גפן 19 עיר: חריש רציף:   קומה:  '}
{'count': 68, 'code': '40461', 'name': 'דרך ארץ/אשל', 'address': ' רחוב:דרך ארץ 5 עיר: חריש רצי

IOPub data rate exceeded.
The notebook server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--NotebookApp.iopub_data_rate_limit`.

Current values:
NotebookApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
NotebookApp.rate_limit_window=3.0 (secs)



## Stops by Frequency in Tel Aviv

In [11]:
from datetime import date
today = int(date.today().strftime("%Y%m%d"))
today_name = date.today().strftime("%A").lower()
trips = session.query(Stop, Trip, Calendar).join(StopTime, Stop.stop_id  == StopTime.stop_id)\
                                           .join(Trip, Trip.trip_id == StopTime.trip_id)\
                                           .join(Calendar, Calendar.service_id == Trip.service_id)\
                                           .filter(Calendar.start_date <= today, Calendar.end_date >= today)\
                                           .filter(Stop.stop_desc.like('%עיר: תל אביב יפו%'))

# I'm sure there's a more efficient way to do this
stops = {}
for stop,trip,calendar in trips.all():
    if not getattr(calendar, today_name): 
        continue
    if stop.stop_id in stops:
        stops[stop.stop_id]['count'] += 1
    else:
        stops[stop.stop_id] = {'count': 1,
                               'code': stop.stop_code,
                               'name': stop.stop_name,
                               'address': stop.stop_desc}

for stop  in sorted(stops.values(), key=lambda r: r['count'], reverse=True):
    print(stop)

{'count': 2553, 'code': '21472', 'name': 'קניון עזריאלי/דרך בגין', 'address': ' רחוב:דרך מנחם בגין  עיר: תל אביב יפו רציף:   קומה:  '}
{'count': 2335, 'code': '21675', 'name': 'גשר קלקא/דרך בגין', 'address': ' רחוב:מרדכי מקלף 5 עיר: תל אביב יפו רציף:   קומה:  '}
{'count': 2084, 'code': '21221', 'name': 'גשר קלקא/דרך בגין', 'address': ' רחוב:דרך מנחם בגין 122 עיר: תל אביב יפו רציף:   קומה:  '}
{'count': 1684, 'code': '21188', 'name': 'דרך נמיר/יהודה המכבי', 'address': ' רחוב:דרך נמיר 127 עיר: תל אביב יפו רציף:   קומה:  '}
{'count': 1680, 'code': '25071', 'name': 'סמינר הקיבוצים/דרך נמיר', 'address': ' רחוב:דרך נמיר  עיר: תל אביב יפו רציף:   קומה:  '}
{'count': 1594, 'code': '21244', 'name': 'דרך בגין/הרכבת', 'address': ' רחוב:דרך מנחם בגין 48 עיר: תל אביב יפו רציף:   קומה:  '}
{'count': 1410, 'code': '23014', 'name': 'קניון עזריאלי/דרך בגין', 'address': ' רחוב:דרך מנחם בגין 132 עיר: תל אביב יפו רציף:   קומה:  '}
{'count': 1398, 'code': '28627', 'name': "ת. מרכזית ת''א ק. 6/הורדה", 'addr